In [29]:
import pandas as pd
import numpy as np
import datetime as dt
import matplotlib.pyplot as plt
import plotly
import plotly.graph_objs as go 
from plotly import tools
from plotly.offline import init_notebook_mode, plot, iplot
import plotly.express as px 

In [30]:
variaveis_medidas = ['Sales', 'Profit', 'Quantity', 'Discount', 'Delivery', 'Price']
variaveis_dimensoes = ['Segment', 'Region', 'Category', 'Sub-Category', 'OYear', 'OMonth']

In [31]:
# data = pd.read_feather('tavbase/Sample.feather')
# data.info()

## Preparação e Tratamento do arquivo Excel para Feather

In [32]:
data = pd.read_excel('tavbase/Sample.xlsx')
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9994 entries, 0 to 9993
Data columns (total 21 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   Row ID         9994 non-null   int64         
 1   Order ID       9994 non-null   object        
 2   Order Date     9994 non-null   datetime64[ns]
 3   Ship Date      9994 non-null   datetime64[ns]
 4   Ship Mode      9994 non-null   object        
 5   Customer ID    9994 non-null   object        
 6   Customer Name  9994 non-null   object        
 7   Segment        9994 non-null   object        
 8   Country        9994 non-null   object        
 9   City           9994 non-null   object        
 10  State          9994 non-null   object        
 11  Postal Code    9994 non-null   int64         
 12  Region         9994 non-null   object        
 13  Product ID     9994 non-null   object        
 14  Category       9994 non-null   object        
 15  Sub-Category   9994 n

In [33]:
data = data.drop(columns=['Row ID', 'Postal Code'])

In [34]:
# ## [DIMENSÕES] Order Date formatter 
data['OYear'] = data['Order Date'].dt.year
data['OMonth'] = data['Order Date'].dt.month
data['OPeriod'] = ((data['OYear'] - data['OYear'].min()) * 12) + data['OMonth']
data['Order Date Month'] = data['Order Date'].apply(lambda x : x.strftime('%Y-%m-01'))

# ## [DIMENSÕES] Ship Date formatter
data['sYear'] = data['Ship Date'].dt.year
data['sMonth'] = data['Ship Date'].dt.month
data['sPeriod'] = ((data['sYear'] - data['sYear'].min()) * 12) + data['sMonth']
data['Ship Date Month'] = data['Ship Date'].apply(lambda x : x.strftime('%Y-%m-01'))

# ## [MEDIDAS] Calcs
data['Delivery'] = (data['Ship Date'] - data['Order Date']).dt.days ## Dias até a entrega
data['Price'] = round((data['Sales'] / data['Quantity']), 2) ## Preço Unitário

# ## [VARIÁVEIS DEPENDENTES]
data['Benefit'] = data['Profit'].apply(lambda x : 1 if x > 0 else 0) ## Lucro?

In [35]:
data.to_feather('tavbase/Sample.feather')

In [36]:
# estados = pd.read_json('csvjson.json')
# estados = estados.drop(columns=['links'])
# estados.to_json('us_states.json')

#Quartis e Outliers

In [37]:
for medida in variaveis_medidas:
    print('=============================')
    print(medida)
    print(data[medida].describe())
    ## Outlier [PARA AVALIAÇÃO]:
    out_min = (data[medida].quantile(0.25) - ( data[medida].quantile(0.75) - data[medida].quantile(0.25) ) * 1.5 )
    out_max = (data[medida].quantile(0.75) + ( data[medida].quantile(0.75) - data[medida].quantile(0.25) ) * 1.5 )
    print('Outlier Mínimo: ', out_min)
    print('Outlier Máximo: ', out_max)

Sales
count     9994.000000
mean       229.858001
std        623.245101
min          0.444000
25%         17.280000
50%         54.490000
75%        209.940000
max      22638.480000
Name: Sales, dtype: float64
Outlier Mínimo:  -271.71000000000004
Outlier Máximo:  498.93
Profit
count    9994.000000
mean       28.656896
std       234.260108
min     -6599.978000
25%         1.728750
50%         8.666500
75%        29.364000
max      8399.976000
Name: Profit, dtype: float64
Outlier Mínimo:  -39.724124999999994
Outlier Máximo:  70.81687499999998
Quantity
count    9994.000000
mean        3.789574
std         2.225110
min         1.000000
25%         2.000000
50%         3.000000
75%         5.000000
max        14.000000
Name: Quantity, dtype: float64
Outlier Mínimo:  -2.5
Outlier Máximo:  9.5
Discount
count    9994.000000
mean        0.156203
std         0.206452
min         0.000000
25%         0.000000
50%         0.200000
75%         0.200000
max         0.800000
Name: Discount, dtype: fl

In [38]:
for dimensao in variaveis_dimensoes :
    print('==> DIMENSÃO {0}'.format(dimensao))
    for medida in variaveis_medidas :
        print('==> MEDIDA {0}'.format(medida))
        print(data.pivot_table(
            index=dimensao,
            values=medida,
            aggfunc=['sum', 'mean', 'count', 'min', 'max']
        ).reset_index())
        ## Quartis e outlies [PARA AVALIAÇÃO]
        q1 = data[medida].quantile(0.25)
        q2 = data[medida].quantile(0.50)
        q3 = data[medida].quantile(0.75)
        print('Primeiro Quartil: < {0}'.format(q1))
        print('Segundo Quartil: de {0} à {1}'.format(q1, q2))
        print('Terceiro Quartil: de {0} à {1}'.format(q2, q3))
        print('Quarto Quartil: > {0}'.format(q3))
        print('Outlier Mínimo: {0}'.format((q1 - (q3 - q1) * 1.5)))
        print('Outlier Máximo: {0}'.format((q1 + (q3 - q1) * 1.5)))

==> DIMENSÃO Segment
==> MEDIDA Sales
       Segment           sum        mean count    min       max
                       Sales       Sales Sales  Sales     Sales
0     Consumer  1.161401e+06  223.733644  5191  0.444  13999.96
1    Corporate  7.061464e+05  233.823300  3020  0.556  17499.95
2  Home Office  4.296531e+05  240.972041  1783  0.990  22638.48
Primeiro Quartil: < 17.28
Segundo Quartil: de 17.28 à 54.489999999999995
Terceiro Quartil: de 54.489999999999995 à 209.94
Quarto Quartil: > 209.94
Outlier Mínimo: -271.71000000000004
Outlier Máximo: 306.27
==> MEDIDA Profit
       Segment          sum       mean  count        min        max
                     Profit     Profit Profit     Profit     Profit
0     Consumer  134119.2092  25.836873   5191 -6599.9780  6719.9808
1    Corporate   91979.1340  30.456667   3020 -3839.9904  8399.9760
2  Home Office   60298.6785  33.818664   1783 -3399.9800  3919.9888
Primeiro Quartil: < 1.72875
Segundo Quartil: de 1.72875 à 8.666499999999996
Te

#RFM

In [39]:
def rfm_variables(df):
    ## FREQUENCY
    f_sales = len(df) ## Quantidade de vendas 
    f_profit = len(df[df['Profit'] > 0]) ## Quantidade de vendas com lucros
    ## MONETARY
    m_sales = round(df['Sales'].sum(), 2) ## Total de vendas
    m_profit = round(df['Profit'].sum(), 2) ## Total de vendas com lucro
    m_quantity = df['Quantity'].sum() ## Total de quantidades
    ## PERIODICITY
    df_sort = df[['Order Date']].sort_values(by='Order Date').drop_duplicates() ## Periodicidade
    df_sort['diff'] = df_sort['Order Date'] - df_sort['Order Date'].shift(1)
    df_sort['diff_int'] = df_sort['diff'].dt.days
    ## REGENCY
    r_days = round(df_sort['diff_int'].mean(), 2)
    return f_sales, f_profit, m_sales, m_profit, m_quantity, r_days

In [40]:
def fit_data(data, variable):
    rfm = pd.DataFrame()
    variables = data[variable].unique()
    for v in variables:
        var = data[data[variable] == v]
        f_sales, f_profit, m_sales, m_profit, m_quantity, r_days = rfm_variables(var)
        rfm = rfm.append(
            {
                'reference': v,
                'm_sales': m_sales,
                'm_profit': m_profit, 
                'm_quantity': m_quantity,
                'r_days': r_days,
                'f_sales': f_sales, 
                'f_profit': f_profit
            },
            ignore_index = True
        )
    return rfm

In [47]:
for dado in ['Ship Mode', 'Segment', 'Region', 'State']: 
    print('===== {} ====='.format(dado))
    rfm_dado = fit_data(data, dado)    
    print(rfm_dado)
    rfm_dado.to_feather('tavbase/rfm_{}.feather'.format(dado))

===== Ship Mode =====
        reference     m_sales   m_profit  m_quantity  r_days  f_sales  \
0    Second Class   459193.57   57446.64        7423    2.31     1945   
1  Standard Class  1358215.74  164088.79       22797    1.34     5968   
2     First Class   351428.42   48969.84        5693    2.63     1538   
3        Same Day   128363.12   15891.76        1960    6.31      543   

   f_profit  
0      1630  
1      4749  
2      1235  
3       444  
===== Segment =====
     reference     m_sales   m_profit  m_quantity  r_days  f_sales  f_profit
0     Consumer  1161401.34  134119.21       19521    1.40     5191      4153
1    Corporate   706146.37   91979.13       11608    1.75     3020      2447
2  Home Office   429653.15   60298.68        6744    2.39     1783      1458
===== Region =====
  reference    m_sales   m_profit  m_quantity  r_days  f_sales  f_profit
0     South  391721.90   46749.43        6209    2.41     1620      1348
1      West  725457.82  108418.45       12266    

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

               reference    m_sales  m_profit  m_quantity  r_days  f_sales  \
0               Kentucky   36591.75  11199.70         523   24.63      139   
1             California  457687.63  76381.39        7667    2.21     2001   
2                Florida   89473.71  -3399.30        1379    7.75      383   
3         North Carolina   55603.16  -7490.91         983   10.66      249   
4             Washington  138641.27  33402.65        1883    6.54      506   
5                  Texas  170188.05 -25729.36        3724    3.73      985   
6              Wisconsin   32114.61   8401.80         463   27.23      110   
7                   Utah   11220.06   2546.53         219   53.16       53   
8               Nebraska    7464.93   2037.09         136   57.00       38   
9           Pennsylvania  116511.91 -15559.96        2153    5.70      587   
10              Illinois   80166.10 -12607.89        1845    5.98      492   
11             Minnesota   29863.15  10823.19         331   32.0

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\duduf\AppData\Local\Temp\ipykernel_15808\3999741325.py:7: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



#Z-Value

In [48]:
group = ['State']
columns = ['Sales', 'Quantity', 'Profit']

result = data.groupby(group)[columns].mean()
result

Sales  Quantity      Profit
State                                                  
Alabama                319.846557  4.196721   94.865989
Arizona                157.508933  3.848214  -15.303235
Arkansas               194.635500  4.000000   66.811452
California             228.729451  3.831584   38.171608
Colorado               176.418231  3.807692  -35.867351
Connecticut            163.223866  3.426829   42.823071
Delaware               285.948635  3.822917  103.930988
District of Columbia   286.502000  4.000000  105.958930
Florida                233.612815  3.600522   -8.875461
Georgia                266.825217  3.831522   88.315453
Idaho                  208.689810  3.047619   39.367767
Illinois               162.939230  3.750000  -25.625787
Indiana                359.431946  3.879195  123.375411
Iowa                   152.658667  3.733333   39.460397
Kansas                 121.429583  3.083333   34.851813
Kentucky               263.250000  3.762590   80.573357
Louisiana              219.453095  3.714286   52.288150
Maine                  158.816250  4.375000   56.810775
Maryland               225.766886  4.000000   66.963608
Massachusetts          212.106919  3.637037   50.262975
Michigan               299.096525  3.709804   95.934069
Minnesota              335.541011  3.719101  121.608847
Mississippi            203.232830  4.169811   59.867475
Missouri               336.441667  3.818182   97.518341
Montana                372.623467  3.733333  122.221900
Nebraska               196.445526  3.578947   53.607742
Nevada                 428.951333  4.307692   85.045279
New Hampshire          270.093481  4.703704   63.203807
New Jersey             275.110092  3.492308   75.176260
New Mexico             129.284378  4.081081   31.273408
New York               275.599531  3.744681   65.637011
North Carolina         223.305880  3.947791  -30.083985
North Dakota           131.415714  4.285714   32.878529
Ohio                   166.861697  3.750533  -36.186304
Oklahoma               298.233182  3.742424   73.544788
Oregon                 140.573790  4.024194   -9.600569
Pennsylvania           198.487077  3.667802  -26.507598
Rhode Island           404.070643  3.553571  130.100523
South Carolina         201.945476  4.095238   42.120395
South Dakota           109.630000  3.500000   32.902358
Tennessee              167.551219  3.721311  -29.189583
Texas                  172.779742  3.780711  -26.121174
Utah                   211.699170  4.132075   48.047802
Vermont                811.760909  4.545455  204.088936
Virginia               315.342500  3.986607   83.026564
Washington             273.994605  3.721344   66.013146
West Virginia          302.456000  4.500000   46.480400
Wisconsin              291.951000  4.209091   76.380004
Wyoming               1603.136000  4.000000  100.196000

In [49]:
zResult = pd.DataFrame()
for col in columns:
    mean = result[col].mean()
    dpadr = result[col].std()
    zResult['z_'+col]= result.apply(lambda x : (x[col] - mean) / dpadr, axis=1)

zResult['score'] = zResult.sum(axis=1)
zResult['rank'] = zResult['score'].rank(ascending=False)
zResult

z_Sales  z_Quantity  z_Profit     score  rank
State                                                               
Alabama               0.194229    1.003619  0.797215  1.995063   5.0
Arizona              -0.532123   -0.062984 -1.354488 -1.949595  38.0
Arkansas             -0.366007    0.401555  0.249285  0.284833  22.0
California           -0.213459   -0.113880 -0.310077 -0.637416  30.0
Colorado             -0.447517   -0.187001 -1.756123 -2.390641  43.0
Connecticut          -0.506553   -1.352630 -0.219230 -2.078412  39.0
Delaware              0.042559   -0.140407  0.974262  0.876414  16.0
District of Columbia  0.045035    0.401555  1.013870  1.460459   9.0
Florida              -0.191609   -0.821044 -1.228948 -2.241601  40.0
Georgia              -0.043006   -0.114071  0.669277  0.512200  18.0
Idaho                -0.303123   -2.513200 -0.286715 -3.103038  48.0
Illinois             -0.507826   -0.363568 -1.556097 -2.427491  44.0
Indiana               0.371347    0.031831  1.354029  1.757208   7.0
Iowa                 -0.553825   -0.414576 -0.284906 -1.253307  34.0
Kansas               -0.693554   -2.403896 -0.374915 -3.472366  49.0
Kentucky             -0.059003   -0.325037  0.518067  0.134028  24.0
Louisiana            -0.254964   -0.472871 -0.034368 -0.762204  32.0
Maine                -0.526274    1.549240  0.053963  1.076929  14.0
Maryland             -0.226714    0.401555  0.252256  0.427097  20.0
Massachusetts        -0.287834   -0.709290 -0.073922 -1.071046  33.0
Michigan              0.101387   -0.486588  0.818075  0.432874  19.0
Minnesota             0.264451   -0.458134  1.319526  1.125844  11.0
Mississippi          -0.327539    0.921262  0.113663  0.707385  17.0
Missouri              0.268481   -0.154898  0.849017  0.962601  15.0
Montana               0.430371   -0.414576  1.331500  1.347294  10.0
Nebraska             -0.357908   -0.887073 -0.008596 -1.253577  35.0
Nevada                0.682400    1.343245  0.605407  2.631053   4.0
New Hampshire        -0.028383    2.555235  0.178824  2.705677   3.0
New Jersey           -0.005937   -1.152233  0.412657 -0.745513  31.0
New Mexico           -0.658409    0.649703 -0.444805 -0.453511  29.0
New York             -0.003747   -0.379847  0.226347 -0.157247  27.0
North Carolina       -0.237726    0.241771 -1.643169 -1.639124  37.0
North Dakota         -0.648873    1.275982 -0.413455  0.213653  23.0
Ohio                 -0.490276   -0.361937 -1.762353 -2.614565  47.0
Oklahoma              0.097524   -0.386753  0.380793  0.091563  26.0
Oregon               -0.607897    0.475599 -1.243110 -1.375407  36.0
Pennsylvania         -0.348773   -0.615133 -1.573319 -2.537226  45.0
Rhode Island          0.571076   -0.964736  1.485376  1.091716  13.0
South Carolina       -0.333299    0.693031 -0.232954  0.126778  25.0
South Dakota         -0.746350   -1.128691 -0.412990 -2.288031  41.0
Tennessee            -0.487191   -0.451369 -1.625701 -2.564260  46.0
Texas                -0.463797   -0.269578 -1.565772 -2.299147  42.0
Utah                 -0.289658    0.805771 -0.117186  0.398927  21.0
Vermont               2.395218    2.070915  2.930436  7.396568   1.0
Virginia              0.174077    0.360567  0.565980  1.100623  12.0
Washington           -0.010928   -0.451270  0.233693 -0.228504  28.0
West Virginia         0.116418    1.931802 -0.147799  1.900421   6.0
Wisconsin             0.069415    1.041476  0.436167  1.547059   8.0
Wyoming               5.936093    0.401555  0.901314  7.238963   2.0

In [50]:
result = result.merge(zResult, right_index=True, left_index=True)
result = result.reset_index()
result.to_feather('tavbase/zresult.feather')
result

State        Sales  Quantity      Profit   z_Sales  \
0                Alabama   319.846557  4.196721   94.865989  0.194229   
1                Arizona   157.508933  3.848214  -15.303235 -0.532123   
2               Arkansas   194.635500  4.000000   66.811452 -0.366007   
3             California   228.729451  3.831584   38.171608 -0.213459   
4               Colorado   176.418231  3.807692  -35.867351 -0.447517   
5            Connecticut   163.223866  3.426829   42.823071 -0.506553   
6               Delaware   285.948635  3.822917  103.930988  0.042559   
7   District of Columbia   286.502000  4.000000  105.958930  0.045035   
8                Florida   233.612815  3.600522   -8.875461 -0.191609   
9                Georgia   266.825217  3.831522   88.315453 -0.043006   
10                 Idaho   208.689810  3.047619   39.367767 -0.303123   
11              Illinois   162.939230  3.750000  -25.625787 -0.507826   
12               Indiana   359.431946  3.879195  123.375411  0.371347   
13                  Iowa   152.658667  3.733333   39.460397 -0.553825   
14                Kansas   121.429583  3.083333   34.851813 -0.693554   
15              Kentucky   263.250000  3.762590   80.573357 -0.059003   
16             Louisiana   219.453095  3.714286   52.288150 -0.254964   
17                 Maine   158.816250  4.375000   56.810775 -0.526274   
18              Maryland   225.766886  4.000000   66.963608 -0.226714   
19         Massachusetts   212.106919  3.637037   50.262975 -0.287834   
20              Michigan   299.096525  3.709804   95.934069  0.101387   
21             Minnesota   335.541011  3.719101  121.608847  0.264451   
22           Mississippi   203.232830  4.169811   59.867475 -0.327539   
23              Missouri   336.441667  3.818182   97.518341  0.268481   
24               Montana   372.623467  3.733333  122.221900  0.430371   
25              Nebraska   196.445526  3.578947   53.607742 -0.357908   
26                Nevada   428.951333  4.307692   85.045279  0.682400   
27         New Hampshire   270.093481  4.703704   63.203807 -0.028383   
28            New Jersey   275.110092  3.492308   75.176260 -0.005937   
29            New Mexico   129.284378  4.081081   31.273408 -0.658409   
30              New York   275.599531  3.744681   65.637011 -0.003747   
31        North Carolina   223.305880  3.947791  -30.083985 -0.237726   
32          North Dakota   131.415714  4.285714   32.878529 -0.648873   
33                  Ohio   166.861697  3.750533  -36.186304 -0.490276   
34              Oklahoma   298.233182  3.742424   73.544788  0.097524   
35                Oregon   140.573790  4.024194   -9.600569 -0.607897   
36          Pennsylvania   198.487077  3.667802  -26.507598 -0.348773   
37          Rhode Island   404.070643  3.553571  130.100523  0.571076   
38        South Carolina   201.945476  4.095238   42.120395 -0.333299   
39          South Dakota   109.630000  3.500000   32.902358 -0.746350   
40             Tennessee   167.551219  3.721311  -29.189583 -0.487191   
41                 Texas   172.779742  3.780711  -26.121174 -0.463797   
42                  Utah   211.699170  4.132075   48.047802 -0.289658   
43               Vermont   811.760909  4.545455  204.088936  2.395218   
44              Virginia   315.342500  3.986607   83.026564  0.174077   
45            Washington   273.994605  3.721344   66.013146 -0.010928   
46         West Virginia   302.456000  4.500000   46.480400  0.116418   
47             Wisconsin   291.951000  4.209091   76.380004  0.069415   
48               Wyoming  1603.136000  4.000000  100.196000  5.936093   

    z_Quantity  z_Profit     score  rank  
0     1.003619  0.797215  1.995063   5.0  
1    -0.062984 -1.354488 -1.949595  38.0  
2     0.401555  0.249285  0.284833  22.0  
3    -0.113880 -0.310077 -0.637416  30.0  
4    -0.187001 -1.756123 -2.390641  43.0  
5    -1.352630 -0.219230 -2.078412  39.0  
6    -0.140407  0.974262  0.876414  16.0  
7     0.401555  1.013870

#Dados Externos


In [45]:
data

Order ID Order Date  Ship Date       Ship Mode Customer ID  \
0     CA-2016-152156 2016-11-08 2016-11-11    Second Class    CG-12520   
1     CA-2016-152156 2016-11-08 2016-11-11    Second Class    CG-12520   
2     CA-2016-138688 2016-06-12 2016-06-16    Second Class    DV-13045   
3     US-2015-108966 2015-10-11 2015-10-18  Standard Class    SO-20335   
4     US-2015-108966 2015-10-11 2015-10-18  Standard Class    SO-20335   
...              ...        ...        ...             ...         ...   
9989  CA-2014-110422 2014-01-21 2014-01-23    Second Class    TB-21400   
9990  CA-2017-121258 2017-02-26 2017-03-03  Standard Class    DB-13060   
9991  CA-2017-121258 2017-02-26 2017-03-03  Standard Class    DB-13060   
9992  CA-2017-121258 2017-02-26 2017-03-03  Standard Class    DB-13060   
9993  CA-2017-119914 2017-05-04 2017-05-09    Second Class    CC-12220   

         Customer Name    Segment        Country             City       State  \
0          Claire Gute   Consumer  United States        Henderson    Kentucky   
1          Claire Gute   Consumer  United States        Henderson    Kentucky   
2      Darrin Van Huff  Corporate  United States      Los Angeles  California   
3       Sean O'Donnell   Consumer  United States  Fort Lauderdale     Florida   
4       Sean O'Donnell   Consumer  United States  Fort Lauderdale     Florida   
...                ...        ...            ...              ...         ...   
9989  Tom Boeckenhauer   Consumer  United States            Miami     Florida   
9990       Dave Brooks   Consumer  United States       Costa Mesa  California   
9991       Dave Brooks   Consumer  United States       Costa Mesa  California   
9992       Dave Brooks   Consumer  United States       Costa Mesa  California   
9993      Chris Cortes   Consumer  United States      Westminster  California   

      ... OMonth OPeriod Order Date Month sYear sMonth  sPeriod  \
0     ...     11      35       2016-11-01  2016     11       35   
1     ...     11      35       2016-11-01  2016     11       35   
2     ...      6      30       2016-06-01  2016      6       30   
3     ...     10      22       2015-10-01  2015     10       22   
4     ...     10      22       2015-10-01  2015     10       22   
...   ...    ...     ...              ...   ...    ...      ...   
9989  ...      1       1       2014-01-01  2014      1        1   
9990  ...      2      38       2017-02-01  2017      3       39   
9991  ...      2      38       2017-02-01  2017      3       39   
9992  ...      2      38       2017-02-01  2017      3       39   
9993  ...      5      41       2017-05-01  2017      5       41   

      Ship Date Month  Delivery   Price  Benefit  
0          2016-11-01         3  130.98        1  
1          2016-11-01         3  243.98        1  
2          2016-06-01         4    7.31        1  
3          2015-10-01         7  191.52        0  
4          2015-10-01         7   11.18        1  
...               ...       ...     ...      ...  
9989       2014-01-01         2    8.42        1  
9990       2017-03-01         5   45.98        1  
9991       2017-03-01         5  129.29        1  
9992       2017-03-01         5    7.40        1  
9993       2017-05-01         5  121.58        1  

[9994 rows x 30 columns]

In [46]:
## Leitura dos dados externos
country = pd.read_json('countries.json', orient='index').reset_index()
cities = pd.read_json('cities.json')

ValueError: Expected object or value

In [ ]:
## Adiciona a sigla do estado às informações
usStates = pd.read_json('us_states.json')
usStates = usStates.rename(columns={
    'usps': 'estado_sigla',
    'name': 'estado'
})
data = data.merge(usStates, left_on=['State'], right_on=['estado'], how='left')
data.drop(columns=['estado'])

Order ID Order Date  Ship Date       Ship Mode Customer ID  \
0     CA-2016-152156 2016-11-08 2016-11-11    Second Class    CG-12520   
1     CA-2016-152156 2016-11-08 2016-11-11    Second Class    CG-12520   
2     CA-2016-138688 2016-06-12 2016-06-16    Second Class    DV-13045   
3     US-2015-108966 2015-10-11 2015-10-18  Standard Class    SO-20335   
4     US-2015-108966 2015-10-11 2015-10-18  Standard Class    SO-20335   
...              ...        ...        ...             ...         ...   
9989  CA-2014-110422 2014-01-21 2014-01-23    Second Class    TB-21400   
9990  CA-2017-121258 2017-02-26 2017-03-03  Standard Class    DB-13060   
9991  CA-2017-121258 2017-02-26 2017-03-03  Standard Class    DB-13060   
9992  CA-2017-121258 2017-02-26 2017-03-03  Standard Class    DB-13060   
9993  CA-2017-119914 2017-05-04 2017-05-09    Second Class    CC-12220   

         Customer Name    Segment        Country             City       State  \
0          Claire Gute   Consumer  United States        Henderson    Kentucky   
1          Claire Gute   Consumer  United States        Henderson    Kentucky   
2      Darrin Van Huff  Corporate  United States      Los Angeles  California   
3       Sean O'Donnell   Consumer  United States  Fort Lauderdale     Florida   
4       Sean O'Donnell   Consumer  United States  Fort Lauderdale     Florida   
...                ...        ...            ...              ...         ...   
9989  Tom Boeckenhauer   Consumer  United States            Miami     Florida   
9990       Dave Brooks   Consumer  United States       Costa Mesa  California   
9991       Dave Brooks   Consumer  United States       Costa Mesa  California   
9992       Dave Brooks   Consumer  United States       Costa Mesa  California   
9993      Chris Cortes   Consumer  United States      Westminster  California   

      ... OPeriod Order Date Month SYear SMonth SPeriod  Ship Date Month  \
0     ...      35       2016-11-01  2016     11      35       2016-11-01   
1     ...      35       2016-11-01  2016     11      35       2016-11-01   
2     ...      30       2016-06-01  2016      6      30       2016-06-01   
3     ...      22       2015-10-01  2015     10      22       2015-10-01   
4     ...      22       2015-10-01  2015     10      22       2015-10-01   
...   ...     ...              ...   ...    ...     ...              ...   
9989  ...       1       2014-01-01  2014      1       1       2014-01-01   
9990  ...      38       2017-02-01  2017      3      39       2017-03-01   
9991  ...      38       2017-02-01  2017      3      39       2017-03-01   
9992  ...      38       2017-02-01  2017      3      39       2017-03-01   
9993  ...      41       2017-05-01  2017      5      41       2017-05-01   

      Delivery   Price  Benefit  estado_sigla  
0            3  130.98        1            KY  
1            3  243.98        1            KY  
2            4    7.31        1            CA  
3            7  191.52        0            FL  
4            7   11.18        1            FL  
...        ...     ...      ...           ...  
9989         2    8.42        1            FL  
9990         5   45.98        1            CA  
9991         5  129.29        1            CA  
9992         5    7.40        1            CA  
9993         5  121.58        1            CA  

[9994 rows x 31 columns]

In [ ]:
## Tratamento dos dados externos

country = country.drop(columns=['native'])
country = country[country['index'] == 'US']
country['capital'] = 'Washington' # Altera a capital de "Washington D.C." para "Washington" para ser relacionado com a cidade da base "cities"

cities = cities[cities['country'] == 'US']

paisDados = cities.groupby('country')['lat', 'lng'].mean()
paisDados = paisDados.reset_index()
paisDados = paisDados.rename(
    columns={
        'lat': 'country_lat',
        'lng': 'country_lng'
    }
)
country = country.merge(paisDados, left_on='index', right_on='country', how='left')
capital = country.merge(cities, left_on=['index','capital'], right_on=['country','name'], how='left')
capital = capital.drop(columns=['country_x','country_y','name_y'])
capital = capital.rename(columns={
    'index': 'pais_sigla',
    'name_x': 'country',
    'lat': 'capital_lat',
    'lng': 'capital_lng'
})
cities = cities.merge(capital, left_on='country', right_on='pais_sigla', how='left')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



In [ ]:
localizacao = pd.DataFrame()
for index, row in data[['City']].drop_duplicates().sort_values(by=['City']).iterrows():
    print('Cidade: {}'.format(row['City']))
    if len(cities[cities['name'] == row['City']]) > 0:
        cidade = cities[cities['name'] == row['City']][['name', 'country_y', 'lat', 'lng']].reset_index()
        cidade = cidade.rename(columns={'name': 'cidade', 'country_y': 'pais'})
        localizacao = localizacao.append(cidade[0:1], ignore_index=True)
    else:
        if len(capital[capital['pais_sigla'] == "US"][:1]) > 0:
            cidade = capital[capital['pais_sigla'] == "US"][['capital', 'country', 'capital_lat', 'capital_lng']].reset_index()
            cidade = cidade.rename(columns={'capital': 'cidade', 'country': 'pais'})
            localizacao = localizacao.append(cidade[0:1], ignore_index=True)
        else:
            print('--------------------------------------------------------------------------------')

Cidade: Aberdeen
Cidade: Abilene
Cidade: Akron
Cidade: Albuquerque
Cidade: Alexandria
Cidade: Allen
Cidade: Allentown
Cidade: Altoona
Cidade: Amarillo
Cidade: Anaheim
Cidade: Andover
Cidade: Ann Arbor
Cidade: Antioch
Cidade: Apopka
Cidade: Apple Valley
Cidade: Appleton
Cidade: Arlington
Cidade: Arlington Heights
Cidade: Arvada
Cidade: Asheville
Cidade: Athens
Cidade: Atlanta
Cidade: Atlantic City
Cidade: Auburn
Cidade: Aurora
Cidade: Austin
Cidade: Avondale
Cidade: Bakersfield
Cidade: Baltimore
Cidade: Bangor
Cidade: Bartlett
Cidade: Bayonne
Cidade: Baytown
Cidade: Beaumont
Cidade: Bedford
Cidade: Belleville
Cidade: Bellevue
Cidade: Bellingham
Cidade: Bethlehem
Cidade: Beverly
Cidade: Billings
Cidade: Bloomington
Cidade: Boca Raton
Cidade: Boise
Cidade: Bolingbrook
Cidade: Bossier City
Cidade: Bowling Green
Cidade: Boynton Beach
Cidade: Bozeman
Cidade: Brentwood
Cidade: Bridgeton
Cidade: Bristol
Cidade: Broken Arrow
Cidade: Broomfield
Cidade: Brownsville
Cidade: Bryan
Cidade: Buffalo
C

In [ ]:
## Relatório de Vendas por País

data = data.merge(localizacao.drop_duplicates(), left_on=['City'], right_on=['cidade'], how='left')
data = data.fillna(0)
pais = data.groupby('Country')['Profit'].sum().reset_index()
fig = px.choropleth(pais,locations='Country',locationmode='country names',color='Profit')
fig.update_layout(title='Vendas por País',template="plotly_dark")
fig.show()

In [ ]:
## Relatório de Vendas por Estado (EUA), por ano

anos = data[['OYear']].sort_values(by=['OYear']).drop_duplicates()['OYear'] ## Adquire os anos contidos nos dados (de forma crescente)

for ano in anos: 
    dataEstado = data[data['OYear'] == ano].groupby('estado_sigla')['Profit'].sum().reset_index()
    fig = px.choropleth(dataEstado,locations='estado_sigla',locationmode='USA-states',color='Profit')
    fig.update_layout(title='Vendas por Estado - {}'.format(ano), geo_scope='usa', template="plotly_dark")
    fig.show()

In [ ]:
m = folium.Map(location=[48, -102], tiles='openstreetmap', zoom_start=3)
for id,row in data.iterrows():
    if id <= 100:
        folium.Marker(location=[row['lat'],row['lng']], popup=row['Profit']).add_to(m)
m        

In [ ]:

datames = data[data['OYear'] == 2016].reset_index()

mc = MarkerCluster()
for idx, row in datames.iterrows():
    if(row['Segment'] == 'Consumer'):
        mc.add_child(folium.Marker([row['lat'], row['lng']],popup=row['Segment'], icon=folium.Icon(color='red', icon='info-sign')))
    elif(row['Segment'] == 'Home Office'):
        mc.add_child(folium.Marker([row['lat'], row['lng']],popup=row['Segment'], icon=folium.Icon(color='green', icon='info-sign')))
    else:
        mc.add_child(folium.Marker([row['lat'], row['lng']],popup=row['Segment'], icon=folium.Icon(color='blue', icon='info-sign')))

mapa = folium.Map(location=[48, -102], tiles='cartodbpositron', zoom_start=3)
mapa.add_child(mc)